<a href="https://colab.research.google.com/github/dharace/COMP8730_Assign01_hirpara3/blob/main/NLP_AS_03.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [28]:
!pip install pytrec_eval
!pip install contractions
!pip install gensim

import pytrec_eval
import pandas as pd
import numpy as np
import json
import os
from os import listdir
from os.path import isfile, join
import csv
import nltk
from nltk.corpus import brown, reuters, gutenberg
from sklearn.feature_extraction.text import CountVectorizer, TfidfTransformer
from sklearn.linear_model import LinearRegression
import contractions
import string
import gensim
from gensim.models import Word2Vec

In [2]:
!git clone https://github.com/dharace/COMP8730_Assign03_hirpara3.git

Cloning into 'COMP8730_Assign03_hirpara3'...
remote: Enumerating objects: 148, done.
remote: Counting objects: 100% (148/148), done.
remote: Compressing objects: 100% (134/134), done.
remote: Total 148 (delta 25), reused 45 (delta 1), pack-reused 0
Receiving objects: 100% (148/148), 264.69 MiB | 23.83 MiB/s, done.
Resolving deltas: 100% (25/25), done.
Checking out files: 100% (44/44), done.


In [3]:
%cd /content/COMP8730_Assign03_hirpara3

/content/COMP8730_Assign03_hirpara3


In [6]:
!ls

code  data  README.md


**Find similarity words using SimLex-999 dataset**

In [14]:
nltk.download('gutenberg')
nltk.download('punkt')
nltk.download('brown')

[nltk_data] Downloading package gutenberg to /root/nltk_data...
[nltk_data]   Unzipping corpora/gutenberg.zip.
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package brown to /root/nltk_data...
[nltk_data]   Unzipping corpora/brown.zip.


True

In [8]:
dataFile = pd.read_csv('data/SimLex-999/SimLex.csv')
dataFile.head(5)

word1        word2 POS  SimLex999  conc(w1)  conc(w2)  concQ  Assoc(USF)  \
0    old          new   A       1.58      2.72      2.81      2        7.25   
1  smart  intelligent   A       9.20      1.75      2.46      1        7.11   
2   hard    difficult   A       8.77      3.76      2.21      2        5.94   
3  happy     cheerful   A       9.55      2.56      2.34      1        5.85   
4   hard         easy   A       0.95      3.76      2.07      2        5.82   

   SimAssoc333  SD(SimLex)  
0            1        0.41  
1            1        0.67  
2            1        1.19  
3            1        2.18  
4            1        0.93

In [9]:
listOfAllWords = dataFile.word1.tolist()
for i,v in enumerate(dataFile.word2.tolist()):
    listOfAllWords.insert(2*i+1,v)
print(listOfAllWords)

['old', 'new', 'smart', 'intelligent', 'hard', 'difficult', 'happy', 'cheerful', 'hard', 'easy', 'fast', 'rapid', 'happy', 'glad', 'short', 'long', 'stupid', 'dumb', 'weird', 'strange', 'wide', 'narrow', 'bad', 'awful', 'easy', 'difficult', 'bad', 'terrible', 'hard', 'simple', 'smart', 'dumb', 'insane', 'crazy', 'happy', 'mad', 'large', 'huge', 'hard', 'tough', 'new', 'fresh', 'sharp', 'dull', 'quick', 'rapid', 'dumb', 'foolish', 'wonderful', 'terrific', 'strange', 'odd', 'happy', 'angry', 'narrow', 'broad', 'simple', 'easy', 'old', 'fresh', 'apparent', 'obvious', 'inexpensive', 'cheap', 'nice', 'generous', 'weird', 'normal', 'weird', 'odd', 'bad', 'immoral', 'sad', 'funny', 'wonderful', 'great', 'guilty', 'ashamed', 'beautiful', 'wonderful', 'confident', 'sure', 'dumb', 'dense', 'large', 'big', 'nice', 'cruel', 'impatient', 'anxious', 'big', 'broad', 'strong', 'proud', 'unnecessary', 'necessary', 'restless', 'young', 'dumb', 'intelligent', 'bad', 'great', 'difficult', 'simple', 'neces

In [33]:
listOfSimLexWords = list(set(listOfAllWords))
print(listOfSimLexWords)

['obvious', 'mouse', 'key', 'spend', 'determine', 'verdict', 'opponent', 'despair', 'bias', 'information', 'win', 'hawk', 'grade', 'lose', 'couple', 'destroy', 'lawyer', 'candidate', 'biography', 'border', 'potato', 'believe', 'companion', 'pretend', 'spirit', 'immoral', 'dictionary', 'furniture', 'army', 'cow', 'summer', 'sickness', 'nephew', 'clue', 'top', 'mother', 'bone', 'throat', 'weather', 'collect', 'lion', 'prestige', 'coast', 'driver', 'husband', 'pursue', 'safety', 'morning', 'anger', 'party', 'proof', 'burial', 'crystal', 'job', 'pot', 'hose', 'wheat', 'costume', 'create', 'newspaper', 'arrive', 'horn', 'mare', 'bunch', 'possess', 'beg', 'church', 'agony', 'archbishop', 'hat', 'pearl', 'deliver', 'knee', 'remind', 'fun', 'participate', 'juice', 'sweater', 'hysteria', 'stud', 'jar', 'friend', 'pollution', 'victor', 'actress', 'lover', 'rain', 'fur', 'topic', 'ashamed', 'ancient', 'trick', 'brow', 'movement', 'meet', 'bed', 'student', 'satisfy', 'profession', 'pair', 'sofa', 

In [10]:
def findWords(word):
    temp = [i for i, x in enumerate(listOfAllWords) if x == word]
    result = []
    for i in temp:
      result.append(listOfAllWords[i+1] if i%2 == 0 else listOfAllWords[i-1])
    return result

In [34]:
def getSimilarWords(word):
    getWords = {}
    topWords = findWords(word)
    max = 10
    levels = [max]*len(topWords)
    for i, w in enumerate(topWords):
        max -= 1
        if i > 10:
            break
        if len(set(topWords))<=10:
            topWords.extend(findWords(w))
            levels.extend([max]*len(findWords(w)))
        else:
            break
    visitedWords = []
    for i, w in enumerate(topWords):
        if w not in visitedWords:
          if len(visitedWords)<10:
            visitedWords.append(i)
    for i in visitedWords: 
        getWords[topWords[i]] = levels[i] 
    return getWords

In [35]:
jsonSimList = {}
for word in listOfAllWords:
    x = getSimilarWords(word)
    if word in x.keys():
      del x[word]
    jsonSimList[word] = x
print(jsonSimList)

{'old': {'new': 7, 'fresh': 9, 'ancient': 9, 'recent': 9, 'wide': 8}, 'new': {'old': 8, 'fresh': 9, 'ancient': 10, 'recent': 10, 'wide': 8, 'modern': 7}, 'smart': {'intelligent': 8, 'dumb': 9, 'stupid': 8, 'foolish': 8, 'dense': 8, 'clever': 8}, 'intelligent': {'smart': 8, 'dumb': 9, 'stupid': 8, 'foolish': 8, 'dense': 8, 'clever': 8}, 'hard': {'difficult': 8, 'easy': 9, 'simple': 9, 'tough': 10, 'dense': 10}, 'difficult': {'hard': 8, 'easy': 9, 'simple': 9, 'tough': 9, 'dense': 9}, 'happy': {'cheerful': 10, 'glad': 10, 'mad': 8, 'angry': 10, 'young': 10, 'delightful': 9}, 'cheerful': {'happy': 7, 'delightful': 10, 'glad': 9, 'mad': 9, 'angry': 9, 'young': 9, 'wonderful': 8}, 'easy': {'hard': 10, 'difficult': 9, 'simple': 9, 'tough': 9, 'flexible': 10, 'big': 10}, 'fast': {'rapid': 4, 'quick': 5}, 'rapid': {'fast': 6, 'quick': 6}, 'glad': {'happy': 8, 'mad': 9, 'cheerful': 9, 'angry': 9, 'young': 9, 'unhappy': 8}, 'short': {'long': 7, 'narrow': 6, 'wide': 7, 'broad': 7, 'dirty': 7}, 'l

 **Tf-iDF using *Gutenberg* and *Brown* corpus**

In [15]:
def processWords(word):
    # lower case word
    word = word.lower()
    # fix contractions
    text = contractions.fix(word)
    # remove punctuations
    text = text.translate(str.maketrans('', '', string.punctuation)) # removing punctuations
    # replace @
    text = text.replace('@', '') 
    return text

In [16]:
def processList(inputlist):
  result = []
  for sentence in inputlist:
    sentence = ' '.join(sentence)
    sentence = processWords(sentence)
    result.append(sentence)
  return result

In [17]:
brownWords = processList(brown.sents())

In [18]:
gutenbergWords = processList(gutenberg.sents('austen-emma.txt'))

In [21]:
# def wordToTfIdf(words, filePath):
def wordToTfIdf(words):
  countVectorizer = CountVectorizer()
  tfidfTransformer = TfidfTransformer()
  tfidfMatrix = tfidfTransformer.fit_transform(countVectorizer.fit_transform(words))
  wordToTfidf = dict(zip(countVectorizer.get_feature_names(), tfidfTransformer.idf_))
#  saveResultToJson(wordToTfidf, filePath)
  return wordToTfidf

In [ ]:
brownWordsJsonTfiDF = wordToTfIdf(brownWords)
brownWordsJsonTfiDF

In [ ]:
gutenbergWordsJsonTfiDF = wordToTfIdf(gutenbergWords)
gutenbergWordsJsonTfiDF

In [121]:
words = list(brownWordsJsonTfiDF.keys())
values = list(brownWordsJsonTfiDF.values())

In [ ]:
jsonSimList = {}
for word in listOfAllWords:
    x = getSimilarWords(word)
    if word in x.keys():
      del x[word]
    jsonSimList[word] = x
print(jsonSimList)

In [144]:
resDict = {}
for w in listOfAllWords:
    df = pd.DataFrame({'words':words, 'values':values})
    if w in words:
        id = words.index(w)
        df['sim'] = df['values'].apply(lambda x: abs(x-values[id]))
        df.sort_values('sim')
        x = df['words'][:10].to_list()
        y = df['values'][:10].to_list()
        z = {}
        for i, word in enumerate(x):
          z[word] = y[i]
        resDict[w] = z
    else:
        resDict[w] = []
resDict

{'old': {'0001': 10.858158890449756,
  '0002': 11.263623998557922,
  '0005': 11.263623998557922,
  '0025in': 11.263623998557922,
  '0039': 11.263623998557922,
  '0043': 11.263623998557922,
  '0075': 11.263623998557922,
  '0080in': 11.263623998557922,
  '01': 9.65418608612382,
  '010': 11.263623998557922},
 'new': {'0001': 10.858158890449756,
  '0002': 11.263623998557922,
  '0005': 11.263623998557922,
  '0025in': 11.263623998557922,
  '0039': 11.263623998557922,
  '0043': 11.263623998557922,
  '0075': 11.263623998557922,
  '0080in': 11.263623998557922,
  '01': 9.65418608612382,
  '010': 11.263623998557922},
 'smart': {'0001': 10.858158890449756,
  '0002': 11.263623998557922,
  '0005': 11.263623998557922,
  '0025in': 11.263623998557922,
  '0039': 11.263623998557922,
  '0043': 11.263623998557922,
  '0075': 11.263623998557922,
  '0080in': 11.263623998557922,
  '01': 9.65418608612382,
  '010': 11.263623998557922},
 'intelligent': {'0001': 10.858158890449756,
  '0002': 11.263623998557922,
  

**Word2Vec find similarity **

In [27]:
window_size = [1, 2, 5, 10]
vector_size = [10, 50, 100, 300]

In [30]:
def buildWord2VecModel(words, fileName):
  for ws in window_size:
    for vs in vector_size:
        word2vecModel = gensim.models.Word2Vec(window=ws, size=vs, workers=5)
        word2vecModel.build_vocab(words)
        # epochs = 1000 takes lot of time to run, reducing this to 10 easily works for testing
        word2vecModel.train(words, total_examples=word2vecModel.corpus_count, epochs=10) 
        word2vecModel.save(fileName + str(ws) + 'VS' + str(vs).format(ws,vs))

In [39]:
buildWord2VecModel(gutenbergWords, 'data/Word2Vec/Guternberg/GutenW2V_WS')

In [40]:
buildWord2VecModel(brownWords, 'data/Word2Vec/Brown/BrownW2V_WS')

In [41]:
gutenFiles = [f for f in listdir('data/Word2Vec/Guternberg') if isfile(join('data/Word2Vec/Guternberg', f))]
gutenFiles

['GutenW2V_WS10VS50',
 'GutenW2V_WS2VS300',
 'GutenW2V_WS2VS100',
 'GutenW2V_WS5VS100',
 'GutenW2V_WS5VS300',
 'GutenW2V_WS2VS50',
 'GutenW2V_WS5VS10',
 'GutenW2V_WS1VS10',
 'GutenW2V_WS10VS300',
 'GutenW2V_WS10VS100',
 'GutenW2V_WS5VS50',
 'GutenW2V_WS1VS50',
 'GutenW2V_WS1VS100',
 'GutenW2V_WS10VS10',
 'GutenW2V_WS2VS10',
 'GutenW2V_WS1VS300']

In [42]:
brownFiles = [f for f in listdir('data/Word2Vec/Brown') if isfile(join('data/Word2Vec/Brown', f))]
brownFiles

['BrownW2V_WS10VS100',
 'BrownW2V_WS2VS300',
 'BrownW2V_WS1VS50',
 'BrownW2V_WS5VS300',
 'BrownW2V_WS2VS50',
 'BrownW2V_WS2VS100',
 'BrownW2V_WS10VS300',
 'BrownW2V_WS1VS100',
 'BrownW2V_WS10VS50',
 'BrownW2V_WS5VS10',
 'BrownW2V_WS5VS100',
 'BrownW2V_WS5VS50',
 'BrownW2V_WS2VS10',
 'BrownW2V_WS10VS10',
 'BrownW2V_WS1VS300',
 'BrownW2V_WS1VS10']

In [51]:
simWords = []
for k,v in jsonSimList.items():
    simWords.append(v)
print(simWords)

[{'new': 7, 'fresh': 9, 'ancient': 9, 'recent': 9, 'wide': 8}, {'old': 8, 'fresh': 9, 'ancient': 10, 'recent': 10, 'wide': 8, 'modern': 7}, {'intelligent': 8, 'dumb': 9, 'stupid': 8, 'foolish': 8, 'dense': 8, 'clever': 8}, {'smart': 8, 'dumb': 9, 'stupid': 8, 'foolish': 8, 'dense': 8, 'clever': 8}, {'difficult': 8, 'easy': 9, 'simple': 9, 'tough': 10, 'dense': 10}, {'hard': 8, 'easy': 9, 'simple': 9, 'tough': 9, 'dense': 9}, {'cheerful': 10, 'glad': 10, 'mad': 8, 'angry': 10, 'young': 10, 'delightful': 9}, {'happy': 7, 'delightful': 10, 'glad': 9, 'mad': 9, 'angry': 9, 'young': 9, 'wonderful': 8}, {'hard': 10, 'difficult': 9, 'simple': 9, 'tough': 9, 'flexible': 10, 'big': 10}, {'rapid': 4, 'quick': 5}, {'fast': 6, 'quick': 6}, {'happy': 8, 'mad': 9, 'cheerful': 9, 'angry': 9, 'young': 9, 'unhappy': 8}, {'long': 7, 'narrow': 6, 'wide': 7, 'broad': 7, 'dirty': 7}, {'short': 7, 'narrow': 6, 'wide': 8, 'broad': 8, 'dirty': 8}, {'dumb': 8, 'smart': 9, 'foolish': 9, 'dense': 9, 'intelligent

In [103]:
def getData(files, fName, path):
  getAllJson = []
  for file in files:
      vect = Word2Vec.load(path + file)
      result = {}
      for i, w in enumerate(listOfSimLexWords):
          try: 
              x = vect.wv.most_similar(w, 10)
          except:
              x = []
          final_words = [m[0] for m in x]
          temp = {}
          for word in simWords[i]:
              if word in final_words:
                  id = final_words.index(word)
                  if id in range(0,3):
                      id2rank = 5
                  elif id in range(3,7):
                      id2rank = 4
                  elif id in range(7,10):
                      id2rank = 3
                  temp[word] = id2rank
              else:
                  temp[word] = 0
          result[w] = temp
      getAllJson.append(result)
  return getAllJson  
              
      # with open(fName.format(f), 'w') as fp:
      #     json.dump(result, fp, indent=4)

In [104]:
gutenWordsJsonW2V = getData(gutenFiles, 'Guternbeg.json', 'data/Word2Vec/Guternberg/')
gutenWordsJsonW2V

[{'obvious': {'ancient': 0, 'fresh': 0, 'new': 0, 'recent': 0, 'wide': 0},
  'mouse': {'ancient': 0,
   'fresh': 0,
   'modern': 0,
   'old': 0,
   'recent': 0,
   'wide': 0},
  'key': {'clever': 0,
   'dense': 0,
   'dumb': 0,
   'foolish': 0,
   'intelligent': 0,
   'stupid': 0},
  'spend': {'clever': 0,
   'dense': 0,
   'dumb': 0,
   'foolish': 0,
   'smart': 0,
   'stupid': 0},
  'determine': {'dense': 0,
   'difficult': 0,
   'easy': 0,
   'simple': 0,
   'tough': 0},
  'verdict': {'dense': 0, 'easy': 0, 'hard': 0, 'simple': 0, 'tough': 0},
  'opponent': {'angry': 0,
   'cheerful': 0,
   'delightful': 0,
   'glad': 0,
   'mad': 0,
   'young': 0},
  'despair': {'angry': 0,
   'delightful': 0,
   'glad': 0,
   'happy': 0,
   'mad': 0,
   'wonderful': 0,
   'young': 0},
  'bias': {'big': 0,
   'difficult': 0,
   'flexible': 0,
   'hard': 0,
   'simple': 0,
   'tough': 0},
  'information': {'quick': 0, 'rapid': 0},
  'win': {'fast': 0, 'quick': 0},
  'hawk': {'angry': 0,
   'cheerful

In [81]:
brownWordsJsonW2V = getData(brownFiles, 'Brown.json', 'data/Word2Vec/Brown/')
brownWordsJsonW2V

[{'obvious': {'ancient': 0, 'fresh': 0, 'new': 0, 'recent': 0, 'wide': 0},
  'mouse': {'ancient': 0,
   'fresh': 0,
   'modern': 0,
   'old': 0,
   'recent': 0,
   'wide': 0},
  'key': {'clever': 0,
   'dense': 0,
   'dumb': 0,
   'foolish': 0,
   'intelligent': 0,
   'stupid': 0},
  'spend': {'clever': 0,
   'dense': 0,
   'dumb': 0,
   'foolish': 0,
   'smart': 0,
   'stupid': 0},
  'determine': {'dense': 0,
   'difficult': 0,
   'easy': 0,
   'simple': 0,
   'tough': 0},
  'verdict': {'dense': 0, 'easy': 0, 'hard': 0, 'simple': 0, 'tough': 0},
  'opponent': {'angry': 0,
   'cheerful': 0,
   'delightful': 0,
   'glad': 0,
   'mad': 0,
   'young': 0},
  'despair': {'angry': 0,
   'delightful': 0,
   'glad': 0,
   'happy': 0,
   'mad': 0,
   'wonderful': 0,
   'young': 0},
  'bias': {'big': 0,
   'difficult': 0,
   'flexible': 0,
   'hard': 0,
   'simple': 0,
   'tough': 0},
  'information': {'quick': 0, 'rapid': 0},
  'win': {'fast': 0, 'quick': 0},
  'hawk': {'angry': 0,
   'cheerful

In [149]:
def getNdcgScoreW2V(files, jsonWords):
  for i, model in enumerate(files):
    temp = jsonWords[i]
    evaluator = pytrec_eval.RelevanceEvaluator(
        jsonSimList, {'ndcg'})

    x = evaluator.evaluate(temp)
    score= []
    for i in x.items():
        score.append((i[1]['ndcg']))

    print("Model " , model, ",", sum(score)/len(score))

In [150]:
getNdcgScoreW2V(gutenFiles, gutenWordsJsonW2V)

Model  GutenW2V_WS10VS50 , 0.004593559066896335
Model  GutenW2V_WS2VS300 , 0.004593559066896335
Model  GutenW2V_WS2VS100 , 0.004593559066896335
Model  GutenW2V_WS5VS100 , 0.004593559066896335
Model  GutenW2V_WS5VS300 , 0.004593559066896335
Model  GutenW2V_WS2VS50 , 0.004593559066896335
Model  GutenW2V_WS5VS10 , 0.004593559066896335
Model  GutenW2V_WS1VS10 , 0.004593559066896335
Model  GutenW2V_WS10VS300 , 0.004593559066896335
Model  GutenW2V_WS10VS100 , 0.004593559066896335
Model  GutenW2V_WS5VS50 , 0.004593559066896335
Model  GutenW2V_WS1VS50 , 0.004593559066896335
Model  GutenW2V_WS1VS100 , 0.004593559066896335
Model  GutenW2V_WS10VS10 , 0.004593559066896335
Model  GutenW2V_WS2VS10 , 0.004593559066896335
Model  GutenW2V_WS1VS300 , 0.004593559066896335


In [151]:
getNdcgScoreW2V(brownFiles, brownWordsJsonW2V)

Model  BrownW2V_WS10VS100 , 0.004593559066896335
Model  BrownW2V_WS2VS300 , 0.004593559066896335
Model  BrownW2V_WS1VS50 , 0.004593559066896335
Model  BrownW2V_WS5VS300 , 0.004593559066896335
Model  BrownW2V_WS2VS50 , 0.004593559066896335
Model  BrownW2V_WS2VS100 , 0.004593559066896335
Model  BrownW2V_WS10VS300 , 0.004593559066896335
Model  BrownW2V_WS1VS100 , 0.004593559066896335
Model  BrownW2V_WS10VS50 , 0.004593559066896335
Model  BrownW2V_WS5VS10 , 0.004593559066896335
Model  BrownW2V_WS5VS100 , 0.004593559066896335
Model  BrownW2V_WS5VS50 , 0.004593559066896335
Model  BrownW2V_WS2VS10 , 0.004593559066896335
Model  BrownW2V_WS10VS10 , 0.004593559066896335
Model  BrownW2V_WS1VS300 , 0.004593559066896335
Model  BrownW2V_WS1VS10 , 0.004593559066896335
